In [1]:
import sys
sys.path.append('D:\\Projects\\nlp-projects\\utils')
print(sys.path)

['C:\\Users\\legion\\AppData\\Local\\Programs\\Python\\Python312\\python312.zip', 'C:\\Users\\legion\\AppData\\Local\\Programs\\Python\\Python312\\DLLs', 'C:\\Users\\legion\\AppData\\Local\\Programs\\Python\\Python312\\Lib', 'C:\\Users\\legion\\AppData\\Local\\Programs\\Python\\Python312', 'd:\\Projects\\nlp-projects\\.venv', '', 'd:\\Projects\\nlp-projects\\.venv\\Lib\\site-packages', 'd:\\Projects\\nlp-projects\\.venv\\Lib\\site-packages\\win32', 'd:\\Projects\\nlp-projects\\.venv\\Lib\\site-packages\\win32\\lib', 'd:\\Projects\\nlp-projects\\.venv\\Lib\\site-packages\\Pythonwin', 'D:\\Projects\\nlp-projects\\utils']


In [18]:
from bs4 import BeautifulSoup
import requests
import json
import os
import re
from dotenv import load_dotenv
from pymongo.mongo_client import MongoClient
from pymongo.server_api import ServerApi
from urllib.parse import quote_plus
from nltk.tokenize import word_tokenize, sent_tokenize, RegexpTokenizer, TreebankWordTokenizer, wordpunct_tokenize
import nltk
from nltk.corpus import stopwords
from nltk.stem.isri import ISRIStemmer
from nltk.stem import WordNetLemmatizer
import clean
import stem
import utils
import tagger
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException
import pandas as pd
import time
from selenium.webdriver.common.action_chains import ActionChains
import pyarabic.araby as araby
from tashaphyne.stemming import ArabicLightStemmer
import qalsadi.lemmatizer
import http.client
from farasa.pos import FarasaPOSTagger 
from farasa.ner import FarasaNamedEntityRecognizer 
from farasa.diacratizer import FarasaDiacritizer 
from farasa.segmenter import FarasaSegmenter 
from farasa.stemmer import FarasaStemmer


In [6]:
def printProgressBar (iteration, total, prefix = '', suffix = '', decimals = 1, length = 100, fill = '█', printEnd = "\r"):
    """
    Call in a loop to create terminal progress bar
    @params:
        iteration   - Required  : current iteration (Int)
        total       - Required  : total iterations (Int)
        prefix      - Optional  : prefix string (Str)
        suffix      - Optional  : suffix string (Str)
        decimals    - Optional  : positive number of decimals in percent complete (Int)
        length      - Optional  : character length of bar (Int)
        fill        - Optional  : bar fill character (Str)
        printEnd    - Optional  : end character (e.g. "\r", "\r\n") (Str)
    """
    percent = ("{0:." + str(decimals) + "f}").format(100 * (iteration / float(total)))
    filledLength = int(length * iteration // total)
    bar = fill * filledLength + '-' * (length - filledLength)
    print(f'\r{prefix} |{bar}| {percent}% {suffix}', end = printEnd)
    # Print New Line on Complete
    if iteration == total: 
        print()

In [15]:
BASE_URL = 'https://www.aljazeera.net'

articles = []
articlesTitles = []
articlesLinks = []
articlesDates = []
articlesContents = []
articlesTopics = ['/news',
                '/where/arab/palestine/',
                '/where/arab/sudan/',
                '/where/europe/ukraine/',
                '/politics/']

In [42]:
driver = webdriver.Chrome()

for topic in articlesTopics:
    driver.get(BASE_URL + topic)
    driver.implicitly_wait(10)

    XPath = '/html/body/div[1]/div/div[3]/div/div[3]/div/div[1]/section/button'
    element = WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.XPATH, XPath)))
    driver.execute_script("arguments[0].scrollIntoView();", element)
    element.click()

    for i in range(50):
        element = WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.XPATH, XPath)))
        driver.execute_script("arguments[0].scrollIntoView();", element)
        element.click()
    
    # get the articles
    temp_articlesLinks = driver.find_elements('xpath', '//a[@class="u-clickable-card__link"]')

    for articleLink in temp_articlesLinks:
        articlesLinks.append(articleLink.get_attribute('href'))

driver.close()

['/news',
 '/where/arab/palestine/',
 '/where/arab/sudan/',
 '/where/europe/ukraine/',
 '/politics/']

In [43]:
len(articlesLinks)

2070

In [47]:
articlesLinks[0]

'https://www.aljazeera.net/news/2024/5/21/%d9%85%d8%ad%d9%83%d9%85%d8%a9-%d9%8a%d9%88%d9%86%d8%a7%d9%86%d9%8a%d8%a9-%d8%aa%d8%a8%d8%b1%d9%89%d8%a1-%d8%aa%d8%b3%d8%b9%d8%a9-%d9%85%d8%aa%d9%87%d9%85%d9%8a%d9%86'

In [74]:
with open('tmp/links.json', 'w', encoding='utf-8') as json_file:
    json.dump(articlesLinks, json_file, indent=4, ensure_ascii=False)

In [59]:
# remove links that dont start with 'https://www.aljazeera.net', revome respectiv title
for link in articlesLinks:
    if not link.startswith('https://www.aljazeera.net'):
        index = articlesLinks.index(link)
        articlesLinks.pop(index)

In [60]:
len(articlesLinks)

2039

In [5]:
with open('tmp/links.json', 'r', encoding='utf-8') as json_file:
    articlesLinks = json.load(json_file)

In [9]:
printProgressBar(0, 500, prefix = 'Progress:', suffix = 'Complete', length = 100)

for i in range(500):
    url = articlesLinks[i]
    html = requests.get(url).text
    soup = BeautifulSoup(html, "html.parser")
    article = ''

    articleDate = soup.select('div[class*="article-dates"]')[0].text

    articleTitle = soup.find('h1').text

    articlesParagraphsContainer = soup.select('div[class*="wysiwyg wysiwyg--all-content"]')[0]

    articlesParagraphs = articlesParagraphsContainer.find_all('p', recursive=False)

    articlesDates.append(articleDate)

    articlesTitles.append(articleTitle)

    for p in articlesParagraphs:
        article += p.text + '\n'

    articlesContents.append(article)

    time.sleep(0.1)
    # Update Progress Bar
    printProgressBar(i + 1, 500, prefix = 'Progress:', suffix = 'Complete', length = 100)

print('Articles dates retrieved!')
print('Articles Contents retrieved!')
for i in range(len(articlesTitles)):
    articles.append({
        'title': articlesTitles[i],
        'link': articlesLinks[i],
        'date': articlesDates[i],
        'content': articlesContents[i]
    })

Progress: |████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% Complete
Articles dates retrieved!
Articles Contents retrieved!


In [10]:
# If you are on Google Colab:
# with open('/content/tmp/aljazzera.json', 'w', encoding='utf-8') as json_file:
with open('tmp/aljazzera.json', 'w', encoding='utf-8') as json_file:
    json.dump(articles, json_file, indent=4, ensure_ascii=False)

In [16]:
# clean memory
del articles
del articlesTitles
del articlesLinks
del articlesDates
del articlesContents
del articlesTopics

In [22]:
with open('tmp/aljazzera.json', 'r', encoding='utf-8') as json_file:
    articles = json.load(json_file)

articles

[{'title': 'تأكيدا لتحقيق الجزيرة.. محكمة يونانية تبرئ 9 مصريين من مسؤولية غرق سفينة لاجئين',
  'link': 'https://www.aljazeera.net/news/2024/5/21/%d9%85%d8%ad%d9%83%d9%85%d8%a9-%d9%8a%d9%88%d9%86%d8%a7%d9%86%d9%8a%d8%a9-%d8%aa%d8%a8%d8%b1%d9%89%d8%a1-%d8%aa%d8%b3%d8%b9%d8%a9-%d9%85%d8%aa%d9%87%d9%85%d9%8a%d9%86',
  'date': '21/5/2024',
  'content': 'برّأت محكمة يونانية اليوم الثلاثاء 9 مصريين متهمين بالتسبب في واحد من أخطر حوادث غرق المهاجرين في البحر الأبيض المتوسط، وذلك في اليوم الأول من محاكمتهم.\nوقال قاضي محكمة كالاماتا (جنوب) إن المحكمة "تعلن تبرئة المتهمين التسعة" وإسقاط كل التهم الموجهة إليهم.\nوبعد مرور حوالي سنة على غرق سفينة الصيد الذي خلّف أكثر من 80 قتيلا وحوالي 600 مفقود، واجه المتهمون التسعة تهمة "تسهيل الدخول غير القانوني للمهاجرين إلى المنطقة" والتسبب بـ"القتل نتيجة الإهمال". كما واجهوا عقوبة السجن مدى الحياة بتهمة "الانتماء إلى منظمة إجرامية". وهم رهن الحبس الاحتياطي منذ 11 شهرا تقريبا.\nوكشف تحقيق للجزيرة منتصف فبراير/شباط الماضي أن جميع المتهمين التسعة لم يكونوا من 

In [19]:
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\legion\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\legion\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\legion\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [33]:
mute_articles = articles

In [34]:
for article in mute_articles:
    article['content'] = clean.remove_punctuations(article['content'])
    article['content'] = clean.remove_diacritics(article['content'])
    article['content'] = clean.normalize_arabic(article['content'])

    stop_words_patterns = r'\b('+ '|'.join(stopword for stopword in stopwords.words('arabic'))+ r')\b'

    article['content'] = re.sub(stop_words_patterns, '', article['content'])
    article['content'] = re.sub(' +', ' ', article['content'])

    # sentence count, split by \n
    article['sentence_count'] = len(article['content'].split('\n'))

    # topic count: the number of occurences of the topic word in the article
    article['topic_count'] = len(re.findall('فلسطين', article['content'])) + len(re.findall('غزه', article['content'])) + len(re.findall('القدس', article['content'])) + len(re.findall('غزة', article['content'])) + len(re.findall('فلسطين', article['title'])) + len(re.findall('غزه', article['title'])) + len(re.findall('القدس', article['title'])) + len(re.findall('غزة', article['title'])) + len(re.findall('رفح ', article['title']))

In [35]:
mute_articles

[{'title': 'تأكيدا لتحقيق الجزيرة.. محكمة يونانية تبرئ 9 مصريين من مسؤولية غرق سفينة لاجئين',
  'link': 'https://www.aljazeera.net/news/2024/5/21/%d9%85%d8%ad%d9%83%d9%85%d8%a9-%d9%8a%d9%88%d9%86%d8%a7%d9%86%d9%8a%d8%a9-%d8%aa%d8%a8%d8%b1%d9%89%d8%a1-%d8%aa%d8%b3%d8%b9%d8%a9-%d9%85%d8%aa%d9%87%d9%85%d9%8a%d9%86',
  'date': '21/5/2024',
  'content': 'برات محكمه يونانيه اليوم الثلاثاء 9 مصريين متهمين بالتسبب اخطر حوادث غرق المهاجرين البحر الابيض المتوسط وذلك اليوم الاول محاكمتهم\nوقال قاضي محكمه كالاماتا جنوب ان المحكمه تعلن تبرءه المتهمين التسعه واسقاط التهم الموجهه اليهم\nوبعد مرور حوالي سنه علي غرق سفينه الصيد اكثر 80 قتيلا وحوالي 600 مفقود واجه المتهمون التسعه تهمه تسهيل الدخول القانوني للمهاجرين الي المنطقه والتسبب بالقتل نتيجه الاهمال واجهوا عقوبه السجن مدي الحياه بتهمه الانتماء الي منظمه اجراميه وهم رهن الحبس الاحتياطي 11 شهرا تقريبا\nوكشف تحقيق للجزيره منتصف فبرايرشباط الماضي ان المتهمين التسعه يكونوا المهربين نظموا الرحله او استفادوا واوضح الاشخاص التسعه حديثهم لمراسلي الجزيره ا

In [39]:
# lemmatize
lemmatizer = qalsadi.lemmatizer.Lemmatizer()

for article in mute_articles:
    article['content'] = re.sub('\n', ' ', article['content'])
    article['content'] = ' '.join([lemmatizer.lemmatize(word) for word in word_tokenize(article['content'])])

In [43]:
# noun count
pos_tagger = FarasaPOSTagger()

printProgressBar(0, 500, prefix = 'Progress:', suffix = 'Complete', length = 100)
for article in mute_articles:
    article['noun_count'] = len(re.findall('NOUN', pos_tagger.tag(article['content'])))
    printProgressBar(mute_articles.index(article) + 1, 500, prefix = 'Progress:', suffix = 'Complete', length = 100)

Progress: |████████████████████████████████████████████████████████████████████████████████████████████████████| 100.0% Complete


In [47]:
mute_articles

[{'title': 'تأكيدا لتحقيق الجزيرة.. محكمة يونانية تبرئ 9 مصريين من مسؤولية غرق سفينة لاجئين',
  'link': 'https://www.aljazeera.net/news/2024/5/21/%d9%85%d8%ad%d9%83%d9%85%d8%a9-%d9%8a%d9%88%d9%86%d8%a7%d9%86%d9%8a%d8%a9-%d8%aa%d8%a8%d8%b1%d9%89%d8%a1-%d8%aa%d8%b3%d8%b9%d8%a9-%d9%85%d8%aa%d9%87%d9%85%d9%8a%d9%86',
  'date': '21/5/2024',
  'content': 'بر محكم يونان يوم ثلاثاء 9 مصري متهم تسبب خطر حوادث غرق مهاجر بحر ابيض متوسط ذلك يوم الاول محاكم قال قاضى محكم كالاماتا جنوب ان المحكمه علن تبرءه متهم التسعه واسقاط تهم الموجهه يهم بعد مرور حوال سن علي غرق سفين صيد كثر 80 قتيل حوال 600 مفقود جهي متهم التسعه تهم تسهيل دخول قانون مهاجر ال المنطقه تسبب قتل نتيجه الاهمال جهي عقوبه سجن مد لحى تهم انتماء ال منظم اجراميه هم رهن حبس احتياط 11 شهر تقريب شف تحقيق للجزيره منتصف فبرايرشباط ماضي ان متهم التسعه كون مهرب نظم الرحله او استفاد واوضح الاشخاص التسعه حديث مراسل الجزيره نهم كانو مجرد ركاب نجو غرق اتهم خفر سواحل يونان تسبب انقلاب قارب مكتظ خبر متهم أمات تبرءتهم مراسل الجزيره شركاء ان ادعاء يونان

In [48]:
with open('tmp/aljazzera_treated.json', 'w', encoding='utf-8') as json_file:
    json.dump(articles, json_file, indent=4, ensure_ascii=False)

In [54]:
# compute scores
from math import log10


for article in mute_articles:
    score = article['sentence_count'] * article['noun_count'] * article['topic_count'] * (10**5)
    article['score'] = log10(score) if score != 0 else 0

In [55]:
mute_articles

[{'title': 'تأكيدا لتحقيق الجزيرة.. محكمة يونانية تبرئ 9 مصريين من مسؤولية غرق سفينة لاجئين',
  'link': 'https://www.aljazeera.net/news/2024/5/21/%d9%85%d8%ad%d9%83%d9%85%d8%a9-%d9%8a%d9%88%d9%86%d8%a7%d9%86%d9%8a%d8%a9-%d8%aa%d8%a8%d8%b1%d9%89%d8%a1-%d8%aa%d8%b3%d8%b9%d8%a9-%d9%85%d8%aa%d9%87%d9%85%d9%8a%d9%86',
  'date': '21/5/2024',
  'content': 'بر محكم يونان يوم ثلاثاء 9 مصري متهم تسبب خطر حوادث غرق مهاجر بحر ابيض متوسط ذلك يوم الاول محاكم قال قاضى محكم كالاماتا جنوب ان المحكمه علن تبرءه متهم التسعه واسقاط تهم الموجهه يهم بعد مرور حوال سن علي غرق سفين صيد كثر 80 قتيل حوال 600 مفقود جهي متهم التسعه تهم تسهيل دخول قانون مهاجر ال المنطقه تسبب قتل نتيجه الاهمال جهي عقوبه سجن مد لحى تهم انتماء ال منظم اجراميه هم رهن حبس احتياط 11 شهر تقريب شف تحقيق للجزيره منتصف فبرايرشباط ماضي ان متهم التسعه كون مهرب نظم الرحله او استفاد واوضح الاشخاص التسعه حديث مراسل الجزيره نهم كانو مجرد ركاب نجو غرق اتهم خفر سواحل يونان تسبب انقلاب قارب مكتظ خبر متهم أمات تبرءتهم مراسل الجزيره شركاء ان ادعاء يونان